# Exercise - Trading Value Stocks

# 1. A Value Strategy

In this exercise, we consider the **price-earnings** ratio of individual stocks in order to invest in **value** securities.

Note that we could consider the full analysis below with other metrics, including the **DP ratio** provided in the same data set. But here, we focus on the **PE ratio**.

<div style="border: 2px solid #0074D9; background: #f0f8ff; padding: 10px; border-radius: 6px;">
  <strong>Note:</strong>  
  Price is what you pay. Value is what you get.<br>
  - Warren Buffett
</div>

#### Data

Use the data in `data/spx_data_weekly.xlsx`.
* `spx data` - time-series data for price, dividend-price ratio, and price-earnings ratio
* `sector data` - ETFs on sub-sectors
* `additional data` - `SPY`, `SHV`, and other benchmarks
* `rates data` - index levels for rates

Risk-free rate could be 
* `SHV`
*  `USGG3M Index` - annualized percent

In [ ]:
import pandas as pd

FILE_DATA = '../data/spx_data_weekly.xlsx'
SHEET_INFO = 'spx names'

info = pd.read_excel(FILE_DATA,sheet_name=SHEET_INFO)
info.set_index('ticker',inplace=True)
info.rename(columns={'security_name':'security name'},inplace=True)

display(info)

name        gics_sector_name       mkt cap
ticker                                                                  
A         Agilent Technologies Inc             Health Care  4.162353e+10
AAPL                     Apple Inc  Information Technology  4.025226e+12
ABBV                    AbbVie Inc             Health Care  4.106695e+11
ABNB                    Airbnb Inc  Consumer Discretionary  7.510938e+10
ABT            Abbott Laboratories             Health Care  2.270793e+11
...                            ...                     ...           ...
XYZ                      Block Inc              Financials  3.675158e+10
YUM                Yum! Brands Inc  Consumer Discretionary  4.137582e+10
ZBH     Zimmer Biomet Holdings Inc             Health Care  1.781850e+10
ZBRA       Zebra Technologies Corp  Information Technology  1.218683e+10
ZTS                     Zoetis Inc             Health Care  5.324455e+10

[503 rows x 3 columns]

In [ ]:
def load_ts(file_data,sheet_name):
    ts = pd.read_excel(file_data,sheet_name=sheet_name,
                    header=[0,1],                  
                    index_col=0)
                    
    ts.columns.names = ["ticker","field"]

    ts.rename(columns={
        'PX_LAST':'price',
        'EQY_DVD_YLD_IND':'dvd yld',
        'PE_RATIO':'pe ratio'
    }, level=1, inplace=True)

    return ts

### 1.0. Data Processing

Filter the data to drop any ticker which does not have at least `5` years of continuous price data.

In [ ]:
MIN_YEARS_REQUIRED = 5

SHEET_TS = 'spx data'
spx_raw = load_ts(FILE_DATA,SHEET_TS)

# Extract price and metric data
px_raw = spx_raw.xs('price', level=1, axis=1)
metric_fields = ['dvd yld', 'pe ratio']
metrics_raw = {}
for field in metric_fields:
    if field in spx_raw.columns.get_level_values(1):
        metrics_raw[field] = spx_raw.xs(field, level=1, axis=1)

# Determine frequency and required periods
freq_str = pd.infer_freq(spx_raw.index)
if freq_str == 'W-FRI' or freq_str == 'W' or (isinstance(freq_str, str) and freq_str.startswith('W')):
    PERIODS = 52  # weekly
elif freq_str == 'M' or freq_str == 'MS' or (isinstance(freq_str, str) and freq_str.startswith('M')):
    PERIODS = 12  # monthly
else:
    PERIODS = 52  # default to weekly

min_periods_required = MIN_YEARS_REQUIRED * PERIODS
print(f"Filtering assets: requiring at least {min_periods_required} periods ({MIN_YEARS_REQUIRED} years) of non-NaN price data...")
print()

# Count non-NaN observations per asset for price
non_nan_counts_price = px_raw.notna().sum()

# Filter: keep only assets with T years of price data
assets_with_sufficient_data = non_nan_counts_price[non_nan_counts_price >= min_periods_required].index.tolist()
assets_dropped = non_nan_counts_price[non_nan_counts_price < min_periods_required].index.tolist()

print(f"Tickers dropped ({len(assets_dropped)}): {sorted(assets_dropped)}")
print()

# Filter spx to only include assets with sufficient data
spx = spx_raw.loc[:, spx_raw.columns.get_level_values(0).isin(assets_with_sufficient_data)]

# Extract filtered price and metrics
px = spx.xs('price', level=1, axis=1)
metrics = {}
for field in metric_fields:
    if field in spx.columns.get_level_values(1):
        metrics[field] = spx.xs(field, level=1, axis=1)

# Ensure all filtered dataframes have same dates (intersection of dates)
common_dates = px.index
for field, metric_df in metrics.items():
    common_dates = common_dates.intersection(metric_df.index)

px = px.loc[common_dates]
for field in metrics:
    metrics[field] = metrics[field].loc[common_dates]

print(f"After filtering to common dates:")
print(f"  Date range: {common_dates.min()} to {common_dates.max()}")
print(f"  Number of dates: {len(common_dates)}")
print()

# Create summary dataframe
summary_data = []

# Raw dimensions
summary_data.append({
    "Dataset": "Raw Price",
    "Rows": px_raw.shape[0],
    "Columns": px_raw.shape[1],
    "Avg NaN per Column": int(round(px_raw.isna().sum().mean())),
    "Date Range": f"{px_raw.index.min().strftime('%Y-%m-%d')} to {px_raw.index.max().strftime('%Y-%m-%d')}"
})

for field, metric_df in metrics_raw.items():
    summary_data.append({
        "Dataset": f"Raw {field}",
        "Rows": metric_df.shape[0],
        "Columns": metric_df.shape[1],
        "Avg NaN per Column": int(round(metric_df.isna().sum().mean())),
        "Date Range": f"{metric_df.index.min().strftime('%Y-%m-%d')} to {metric_df.index.max().strftime('%Y-%m-%d')}"
    })

# Filtered dimensions
summary_data.append({
    "Dataset": "Filtered Price",
    "Rows": px.shape[0],
    "Columns": px.shape[1],
    "Avg NaN per Column": int(round(px.isna().sum().mean())),
    "Date Range": f"{px.index.min().strftime('%Y-%m-%d')} to {px.index.max().strftime('%Y-%m-%d')}"
})

for field, metric_df in metrics.items():
    summary_data.append({
        "Dataset": f"Filtered {field}",
        "Rows": metric_df.shape[0],
        "Columns": metric_df.shape[1],
        "Avg NaN per Column": int(round(metric_df.isna().sum().mean())),
        "Date Range": f"{metric_df.index.min().strftime('%Y-%m-%d')} to {metric_df.index.max().strftime('%Y-%m-%d')}"
    })

summary_df = pd.DataFrame(summary_data).set_index("Dataset")
display(summary_df.style.set_caption("Data Filtering Summary"))

print()
display(spx.tail().style.format('{:.2f}',na_rep='').format_index(lambda x: x.strftime('%Y-%m-%d')))

Filtering assets: requiring at least 260 periods (5 years) of non-NaN price data...

Tickers dropped (15): ['ABNB', 'APP', 'CEG', 'COIN', 'DASH', 'EXE', 'GEHC', 'GEV', 'HOOD', 'KVUE', 'PLTR', 'SOLV', 'SW', 'VLTO', 'WBD']

After filtering to common dates:
  Date range: 2015-07-03 00:00:00 to 2025-06-27 00:00:00
  Number of dates: 522



### 1.1. Examples and Outliers

Report the highest and lowest **price-earning** stocks...

* for any given date across the entire panel
* taking an average of the past year

Which stocks were they? Was it driven more by changes in `P` or `E`?

### 1.2. A Value Strategy

For this strategy, use the `pe ratio` data.

Build a portfolio where at every time $t$, you set weights, $w_t$ that invest...
* long the **lowest** ranking `20%` stocks.

For now, go equal weights of `0.01` in any stock for which you're long or short. 

#### Realized Returns
Start at the beginning of the sample.
* At time $t$, rank the stocks. 
* The selected stocks will earn $r_{t+1}$.

### 1.3. Long-Short

Re-do the strategy of the previous section, but this time go long and short...

At any given time $t$, set the vector $w_t$ as follows...
* **long** the **lowest**-ranking `20%` of stocks.
* **short** the **highest**-ranking `20%` of stocks.
* take no position in all other stocks.

### 1.4. Performance

Calculate the return of your portfolio over time. 

Report the following annualized stats
* mean
* volatility
* Sharpe 

#### Annualizing
Annualize the stats by scaling
* mean by 52
* vol by $\sqrt{52}$
* Sharpe by $\sqrt{52}$

#### Sharpe Ratio
One of the most commonly cited performance statistics is the Sharpe ratio.

$$\text{Sharpe} = \frac{\mu}{\sigma}$$

Technically, this is defined where $\mu$ and $\sigma$ are the mean and vol of the **excess** returns. Here, you're welcome to subtract the risk-free rate from all returns to make these excess, but no need to do so.

### 1.5 Comparison

Compare the stats of `1.4` with the same stats for `SPY`, found in the `additional data` tab.

In [ ]:
SHEET_BENCH = 'additional data'
bench = load_ts(FILE_DATA,SHEET_BENCH)
display(bench[['SPY']].tail().style.format('{:.2f}',na_rep='').format_index('{:%Y-%m-%d}'))

***

# 2. Attribution

### 2.1. Market Exposure

For both the long-only (LO) and long-short (LS) strategies, estimate a linear factor decomposition (LFD) against `SPY`

Report the...
* alpha (annualized)
* beta
* r-squared

Also show the correlation matrix of the strategies.

How do the LO and LS strategies compare to `SPY`?

### 2.2. Sector Regression

Estimate a multivariate LFD for both LO and LS against all the sector ETFs.
* Note that `SHV` is not a sector ETF but rather a money-market fund. Exclude it.
* Exclude `SPY`.

Report the same stats as in `2.1.`

In [ ]:
SHEET_SECTOR_INFO = 'sector names'
info_sectors = pd.read_excel(FILE_DATA,sheet_name=SHEET_SECTOR_INFO).rename(columns={'Unnamed: 0':'ticker'}).set_index('ticker').drop(columns=['gics_sector_name'])
info_sectors['cur_mkt_cap'] = info_sectors['cur_mkt_cap'].astype(float) / 1e9
info_sectors.rename(columns={'cur_mkt_cap':'fund size ($ billions)'},inplace=True)
display(info_sectors.style.format({'fund size ($ billions)':'${:,.2f}'}))

In [ ]:
SHEET_SECTORS = 'sector data'
sectors = load_ts(FILE_DATA,SHEET_SECTORS)
display(sectors.tail().style.format('{:.1f}',na_rep='').format_index(lambda x: x.strftime('%Y-%m-%d')))

### 2.3. Sector Neutrality

Is your LO or LS implementation of the strategy neutral to sectors? To which sector does it have the largest exposure?

**Remember**

Unless regressors are standardized, comparing betas directly can be misleading. You might consider comparing $\beta_i\sigma_i$ when deciding which exposure is most substantial.

### 2.4. Magnificent Seven

Construct an equally-weighted portfolio of the following tickers. Call this `MAG`. Estimate a LFD on both `SPY` and `MAG`. Do this for both the LO and LS strategies.

Report the stats from `2.1`.

Comment on what you conclude from this regression.

In [ ]:
TICKS_MAG = ['AAPL','MSFT','GOOG','AMZN','NVDA','META','TSLA']
display(TICKS_MAG)

['AAPL', 'MSFT', 'GOOG', 'AMZN', 'NVDA', 'META', 'TSLA']

***